In [1]:
#Let's import the necessary modules
import numpy as np
import math 
import pandas as pd
import matplotlib.pyplot as plt
import pylab as pl
from sklearn.neighbors import NearestNeighbors
import astropy.units as u
from astropy.table import QTable, Table, Column
from astropy.coordinates import SkyCoord

In [1]:
#Let's define the necessary functions

#Function that takes the coordinates RA,DEC of two stars as input and returns the coordinates RA,DEC of their midpoint
def coord_midpoint(RA1,DEC1,RA2,DEC2): #RA,DEC are the coord of the two stars forming the BS

  RA_12=(RA1+RA2)/2
  DEC_12=(DEC1+DEC2)/2
  return RA_12, DEC_12 #The function returns the coord RA,DEC of the star in the middle point

#This function runs the KNN algorithm: takes as input the 'catalogue' of stars for which it has to find the nearest ones and the separation[AU]
#returns the separation between the stars, the index of the first and the index of the second star
def KNN_Alg(data, separation): #the input "data" (shape=array) contains the info needed by KNN (i.e. coord RA,DEC of the targets)
  dist = [] #List that will contain the distances between the stars. Using as input (RA,DEC), this distance will be in Degree
  dist_AU = [] #List that will contain the distances in AU between the stars
  #Let's find the 2 nearest neighbors. Since we are looking for pairs in the same catalogue the first neighbour of the star is itself
  neigh = NearestNeighbors(n_neighbors=2)
  neigh.fit(data)
  #I will increase the separation each step
  Sep_AU = [] #List that will contain only the value < separation
  KNN_ind0 = [] #List that will contain the indices in Vision of the central star (system for which distance between the 2stars < separation)
  KNN_ind1 = [] #List that will contain the indices in Vision of the nearest neighbor star (system for which distance between the 2stars < separation)
  for j,i in enumerate(data): #for every star in Vision Catalogue find out (2) nearest neighbors
      print('Star {}'.format(j),neigh.kneighbors([i])) #output: Star number [distances of nN][indices of nN]
      distance=neigh.kneighbors([i])[0][0] #neigh.kneighbors([i]) is a tuple, I want only the 1st array, i.e. distances
      ind=neigh.kneighbors([i])[1][0] #neigh.kneighbors([i]) is a tuple, I want only the 2nd array, i.e. index of the nearest neighbor
      dist.append(distance[1]*0.0174533*400) #distance[1] is in degree, multiplying this value by 0.017.. we get radians, finally multiplying by 400 we get parsecs
      dist_AU.append(dist[j]*206265) #dist[j] is in parsec. Multiplying this value by 206265 we get AU
      if dist_AU[j]<=separation:
        Sep_AU.append(dist_AU[j])
        #For each star, I need the index of the nearest neighbour printed by KNN
        KNN_ind0.append(ind[0]) #Star 1 Index
        KNN_ind1.append(ind[1]) #Star 2 Index

  #Convert lists into arrays (for the next steps it is better to work with arrays)
  Sep_AU = np.array(Sep_AU)
  KNN_ind0 = np.array(KNN_ind0)
  KNN_ind1 = np.array(KNN_ind1)

  #Removing pairs counted twice, i.e. the pair A-B and the pair B-A are the same
  indx_del = [] #Empty list that will contain one of the two positions of the pairs counted twice
  for i in range(len(KNN_ind1)):
    if (i in indx_del)==False:
      for j in range(len(KNN_ind0)):
        if KNN_ind1[i]==KNN_ind0[j] and KNN_ind1[j]==KNN_ind0[i]:
          indx_del.append(j)

  #len(indx_del) = Number of identical pairs, i.e. number of pairs that have been eliminated
  new_Sep_AU = np.zeros(len(Sep_AU)-len(indx_del), dtype=float)
  new_KNN_ind0 = np.zeros(len(KNN_ind0)-len(indx_del), dtype=int)
  new_KNN_ind1 = np.zeros(len(KNN_ind1)-len(indx_del), dtype=int)

  new_Sep_AU = np.delete(Sep_AU, indx_del) #Separation between the star forming the Binary System
  new_KNN_ind0 = np.delete(KNN_ind0, indx_del) #Star1 (in the BS) Index in Vision
  new_KNN_ind1 = np.delete(KNN_ind1, indx_del) #Star2 (in the BS) Index in Vision

  return new_Sep_AU[:], new_KNN_ind0[:], new_KNN_ind1[:]

#Function for calculating the coordinates of Single Stars
#INPUT: complete list of objects we are working with, OUTPUT: RA,DEC coordinates of single stars, correctly dimensioned
def coord_single_star(catalogue, delet_ind):
  #We need the coord (RA,DEC) of all Single stars (we will need them for the KNN algorithm)
  #This information is contained in the catalogue, we just need to consider the right targets
  Coord_RA=np.zeros(len(catalogue), dtype=float)
  Coord_DEC=np.zeros(len(catalogue), dtype=float)
  for i in range(len(Coord_RA)):
    Coord_RA[i]=catalogue[i][0]
    Coord_DEC[i]=catalogue[i][1]

  single_RA = np.zeros(len(catalogue)-len(delet_ind), dtype=float)
  single_DEC = np.zeros(len(catalogue)-len(delet_ind), dtype=float)
  single_RA = np.delete(Coord_RA, delet_ind)
  single_DEC = np.delete(Coord_DEC, delet_ind)

  #In order to use the KNN alg again, we need to reshape our data
  #We want to create an array with dimensions (len(single_ind), 2), i.e. an array that for each Single star contains a 2nd array with 2 elements: RA,DEC
  single_star = []
  for i in range(len(single_RA)):
    single_star.append(single_RA[i])
    single_star.append(single_DEC[i])

  single_star = np.reshape(single_star, (len(single_RA),2))

  return single_star[:]

#Function that takes as input the list of indices of all initial objects used for KNN, the indices of stars1 in the BS, the indices of stars2 in the BS, the catalogue i.e. the list with all the targets, step=iteration number
#This function returns the indices and the coord. of the Single Star, correctly resized
def single_star(ind_cat, ind_star1, ind_star2, catal):
  #We need to remove from the initial catalogue all indices that appear in the BSs
  #Let's construct a single array in which we insert all and only the star indices that make up the BS
  tot_ind=np.concatenate((ind_star1,ind_star2)) #Array in which we save both the index of Star1 and the index of Star2

  #It's possible that the same star forms different BS. There is no point in considering the same index twice
  #In order to remove the duplicates we can use the built-in command set(). In order to use that, we need a list
  list_tot_ind=tot_ind.tolist()
  final_list_tot_ind=list(set(list_tot_ind))
  final_list_tot_ind.sort() #We sort the remaining indices in ascending order
  final_tot_ind=np.array(final_list_tot_ind) #Array that contains all the indices of the Binary Stars

  sin_ind=np.delete(ind_cat, final_tot_ind) #Array that contains the indices of the Single Stars
  #zero = np.zeros(len(sin_ind)) #If we have a Single Star the 2nd index must be NaN (i.e. NO STAR)
  #zero[:] = np.nan
  single_ind = []
  for i in range(len(sin_ind)):
    single_ind.append(sin_ind[i])
    single_ind.append('NaN')

  #We need to reshape our indices in this way for later
  single_ind = np.reshape(single_ind, (len(sin_ind),2))

  single_coord = coord_single_star(catal, final_tot_ind)

  return single_ind[:], single_coord[:]

#Function for calculating the coordinates of the New Stars
#INPUT: List(=catalogue) of objects we are working with, OUTPUT: indices and RA,DEC coordinates of the New Star, correctly dimensioned
def coord_new_star(catalogue, ind_star1, ind_star2):
  first_RA = np.zeros(len(ind_star1), dtype=float) #RA coord. for Star1 in the BS
  first_DEC = np.zeros(len(ind_star1), dtype=float) #DEC coord. for Star1 in the BS
  second_RA = np.zeros(len(ind_star2), dtype=float) #RA coord. for Star2 in the BS
  second_DEC = np.zeros(len(ind_star2), dtype=float) #DEC coord. for Star2 in the BS
  for i in range(len(ind_star1)):
    first_RA[i] = catalogue[ind_star1[i]][0]
    first_DEC[i] = catalogue[ind_star1[i]][1]
    second_RA[i] = catalogue[ind_star2[i]][0]
    second_DEC[i] = catalogue[ind_star2[i]][1]

  first_star = []
  second_star = []
  for i in range(len(first_RA)):
    first_star.append(first_RA[i])
    first_star.append(first_DEC[i])
    second_star.append(second_RA[i])
    second_star.append(second_DEC[i])

  first_star = np.reshape(first_star, (len(first_RA),2))
  second_star = np.reshape(second_star, (len(second_RA),2))

  #Let's find the coord (RA,DEC) of the New Star which is positioned at the midpoint of the segment joining the two stars of the BS
  newstar_Ra = np.zeros(len(first_RA), dtype=float)
  newstar_Dec = np.zeros(len(first_DEC), dtype=float)
  for i in range(len(first_RA)):
    newstar_Ra[i],newstar_Dec[i]=coord_midpoint(first_RA[i],first_DEC[i],second_RA[i],second_DEC[i])

  #Let's reshape the coord as usual
  new_star = []
  for i in range(len(newstar_Ra)):
    new_star.append(newstar_Ra[i])
    new_star.append(newstar_Dec[i])

  new_star = np.reshape(new_star, (len(newstar_Ra),2))

  #Let's create an array that will contains the index of the New Star, i.e. a pair formed by the indices of the stars that compose the BS
  newstar_ind = []
  for i in range(len(ind_star1)):
    newstar_ind.append(ind_star1[i])
    newstar_ind.append(ind_star2[i])

  newstar_ind = np.array(newstar_ind)
  newstar_ind = np.reshape(newstar_ind, (len(ind_star1),2))

  return new_star[:], newstar_ind[:]


Mounted at /content/drive


In [2]:
#This function returns the FREQUENCY, i.e. fractions of systems that are multiple
#s=number of single stars, b=number of binaries, t=number of triples etc. 
def frequency(s,b,t,q,f,sis,sev,e):
  MF = (b+t+q+f+sis+sev+e)/(s+b+t+q+f+sis+sev+e)
  return MF

#This function returns the COMPANION FRACTION, i.e. the average number of companions per system
def companion_fraction(s,b,t,q,f,sis,sev,e):
  CF = (b+2*t+3*q+4*f+5*sis+6*sev+7*e)/(s+b+t+q+f+sis+sev+e)
  return CF

#Uncertanties on the MF and CF (here indicate with x) are calculated using the Wilson Score Interval
def uncertainty(x,s,b,t,q):
  Nsys = s+b+t+q
  z = 1
  sigma_plus = (1/(1+(z**2/Nsys)))*(x+(z**2/(2*Nsys))) + (z/(1+(z**2/Nsys)))*((((x*(1-x))/Nsys)+(z**2/(4*Nsys)))**(1/2))
  sigma_minus = (1/(1+(z**2/Nsys)))*(x+(z**2/(2*Nsys))) - (z/(1+(z**2/Nsys)))*((((x*(1-x))/Nsys)+(z**2/(4*Nsys)))**(1/2))
  return sigma_plus, sigma_minus
#NOTE: if CF>0 or CF tends to 0, instead of using this formula we have to use Poisson Statistics --> Use Poisson for calculating sigma when CF>0.5

In [3]:
#Probability

#1) Estimate the typical YSO surface density. Using the KNN alg., Σ = 10/Area where 10=number of nearest neighbors, Area=pi*(R10**2) with R10=radius of the 11th neig.
#Let's use the VisionIII catalogue (In the paper they use the Megath 2012 Catalogue)
def surface_density(catalogue):
  Distance = [] #List that will contain the distances between the stars. Using as input (RA,DEC), this distance will be in Degree
  Distance_AU = [] #List that will contain the distances in AU between the stars
  #Let's find the 10 nearest neighbors. Since we are looking for pairs in the same catalogue the first neighbour of the star is itself
  neighbors = NearestNeighbors(n_neighbors=11)
  neighbors.fit(catalogue)
  surface_density = []
  for j,i in enumerate(catalogue): #for every star in Vision Catalogue find out (2) nearest neighbors
      print('Star {}'.format(j),neighbors.kneighbors([i])) #output: Star number [distances of nN][indices of nN]
      distances=neighbors.kneighbors([i])[0][0] #neigh.kneighbors([i]) is a tuple, I want only the 1st array, i.e. distances
      indices=neighbors.kneighbors([i])[1][0] #neigh.kneighbors([i]) is a tuple, I want only the 2nd array, i.e. index of the nearest neighbor
      Distance.append(distances[10]*0.0174533*400) #distance[1] is in degree, multiplying this value by 0.017.. we get radians, finally multiplying by 400 we get parsecs
      Distance_AU.append(Distance[j]*206265) #dist[j] is in parsec. Multiplying this value by 206265 we get AU
      surface_density.append(10/((math.pi)*(Distance[j]**2)))
  
  return surface_density[:], Distance[:]

def comp_prob(density, d):
  lam = density*(math.pi)*(d**2)
  P = math.exp(-lam)
  return P

'''
def probability_unassociated(density, d):
  lam = 0.9*density*(math.pi)*(d**2)
  P = 1 - math.exp(-lam)
  return P

def companion_detection(CF, density, d):
  lam = 0.9*density*(math.pi)*(d**2)
  P_det_comp = 0.9
  P_comp = CF
  P_det = (0.9*P_comp) + (1-math.exp(-lam))*(1-(0.9*P_comp))
  P_comp_det = (P_det_comp*P_comp)/P_det
  return P_comp_det
'''

'\ndef probability_unassociated(density, d):\n  lam = 0.9*density*(math.pi)*(d**2)\n  P = 1 - math.exp(-lam)\n  return P\n\ndef companion_detection(CF, density, d):\n  lam = 0.9*density*(math.pi)*(d**2)\n  P_det_comp = 0.9\n  P_comp = CF\n  P_det = (0.9*P_comp) + (1-math.exp(-lam))*(1-(0.9*P_comp))\n  P_comp_det = (P_det_comp*P_comp)/P_det\n  return P_comp_det\n'

In [4]:
from google.colab import drive #Mounting google drive. Insert confirmation code.
drive.mount('/content/drive') 
#we load the VisionIII catalogue, in particular we are only taking RA and DEC as input 
Vision = [] #Vision catalogue/sources for which I want to find the companion 
file = open('/content/drive/My Drive/Vision_Cat', 'r') #reading out second data set
for i, line in enumerate(file.readlines()):
    if i==0: 
        continue
    line = line.split()
    line[0]=float(line[0]) #RA
    line[1]=float(line[1]) #DEC
    Vision.append(line[0:2])
    file.close()

Vision = np.array(Vision) #reshape to an np.array so that it can be handled by sklearn 

Drive already mounted at /content/drive; to attempt to forcibly remount, call drive.mount("/content/drive", force_remount=True).


In [5]:
#List1 contains the YSO surface densities for each star in VisionIII catalogue, List2 contains the distances of the 11-th neighbors
surface_density_YSO, R_10 = surface_density(Vision) 
#density = [#obj / pc^2], R_10 = [pc]
print(surface_density_YSO)
print(R_10)
mean = 0
for i in range(len(surface_density_YSO)):
  mean += surface_density_YSO[i]
mean_surface_density = mean/(len(surface_density_YSO)) #This value represents the mean value of the surface density

print(mean_surface_density)

Output streaming troncato alle ultime 5000 righe.
        0.0179359 ]]), array([[1451, 1464, 1428, 1526, 1375, 1491, 1467, 1316, 1469, 1399, 1457]]))
Star 1452 (array([[0.        , 0.01032376, 0.01049236, 0.02000072, 0.02417176,
        0.02717018, 0.02868792, 0.03019974, 0.03331769, 0.035477  ,
        0.03574973]]), array([[1452, 1380, 1475, 1483, 1345, 1292, 1246, 1665, 1203, 1654, 1100]]))
Star 1453 (array([[0.        , 0.01554124, 0.01849339, 0.01915294, 0.01934567,
        0.01935058, 0.01995336, 0.02068703, 0.02458581, 0.03036318,
        0.03114733]]), array([[1453, 1557, 1522, 1394, 1289, 1296, 1561, 1405, 1341, 1462, 1406]]))
Star 1454 (array([[0.        , 0.01979655, 0.02101265, 0.02206404, 0.02224523,
        0.02670552, 0.02872595, 0.02886449, 0.02892554, 0.03010233,
        0.03238417]]), array([[1454, 1307, 1560, 1301, 1285, 1241, 1361, 1625, 1589, 1221, 1645]]))
Star 1455 (array([[0.        , 0.01513918, 0.01696763, 0.01871623, 0.02112926,
        0.02344705, 0.02563576

In [6]:
#Let's compute the Surface Density for the SODA catalogue

Soda_coord = [] #Vision catalogue/sources for which I want to find the companion 
file = open('/content/drive/My Drive/SODA_Coordinates', 'r') #reading out second data set
for i, line in enumerate(file.readlines()):
    if i==0: 
        continue
    line = line.split()
    line[0]=float(line[0]) #RA
    line[1]=float(line[1]) #DEC
    Soda_coord.append(line[0:2])
    file.close()

Soda_coord = np.array(Soda_coord) #reshape to an np.array so that it can be handled by sklearn 

In [7]:
#List1 contains the YSO surface densities for each star in VisionIII catalogue, List2 contains the distances of the 11-th neighbors
soda_density, R_10_soda = surface_density(Soda_coord) 
#density = [#obj / pc^2], R_10 = [pc]
print(soda_density)
print(R_10_soda)
mean1 = 0
for i in range(len(soda_density)):
  mean1 += soda_density[i]
mean_soda_density = mean1/(len(soda_density)) #This value represents the mean value of the surface density

print(mean_soda_density)

Star 0 (array([[0.        , 0.08947784, 0.12188542, 0.12474428, 0.13759679,
        0.13841297, 0.14953913, 0.14972743, 0.15126708, 0.1514948 ,
        0.15162268]]), array([[ 0,  2,  3,  7,  8,  1, 13, 12, 14, 15, 16]]))
Star 1 (array([[0.        , 0.06987097, 0.07111871, 0.07253621, 0.09328802,
        0.09644971, 0.1039747 , 0.11419675, 0.11971947, 0.12512664,
        0.12587355]]), array([[ 1,  4,  5,  6,  9, 10,  8, 21,  3,  7, 28]]))
Star 2 (array([[0.        , 0.03863406, 0.03927149, 0.06053558, 0.0620534 ,
        0.06244271, 0.06350702, 0.06361769, 0.06381406, 0.06552686,
        0.07595209]]), array([[ 2,  3,  7, 12, 13, 15, 16,  8, 17, 14, 22]]))
Star 3 (array([[0.        , 0.00548991, 0.02761042, 0.03449971, 0.03512747,
        0.03863406, 0.04342005, 0.04452244, 0.04523363, 0.04619565,
        0.05189235]]), array([[ 3,  7,  8, 12, 15,  2, 19, 17, 22, 20, 16]]))
Star 4 (array([[0.        , 0.001302  , 0.00880565, 0.03381585, 0.03618174,
        0.04869243, 0.05933017, 0.06

In [57]:
print(soda_density)
print(surface_density_YSO)

[2.8408396521782207, 4.121981687777185, 11.321280996760214, 24.253165191338233, 8.370354008202499, 8.56187836008496, 9.578331554036602, 30.30318160197687, 25.166707884695356, 14.79941943227058, 15.745315839811536, 10.358551625787577, 75.75201794120797, 34.09279232777422, 31.09845604794956, 72.70200395888234, 40.923933776540956, 62.81371618077557, 5.631299878972446, 61.4069622389423, 39.236588313164816, 7.415834927183453, 94.19859734813313, 16.17037457689376, 14.7001946777406, 87.48833733158274, 33.90818059308033, 70.07382092936645, 8.921796579815739, 82.98072135971303, 60.604849782864534, 18.733043417432917, 62.959575560100106, 54.3508176404968, 45.22783044674023, 29.365040972031984, 9.453875743208632, 10.090270520466714, 23.46535635056739, 13.563643906729963, 9.356519383002263, 6.293619746883848, 9.456664250266511, 9.21565806774418, 17.337385185830467, 9.091649260135636, 16.386486089907606, 9.21565806774418, 12.071456828783589, 3.526336373220705, 6.293619746883848, 8.383645204272788, 

In [8]:
#STEP 0
New_Sep_AU = []
New_KNN_ind0 = []
New_KNN_ind1 = []
New_Sep_AU, New_KNN_ind0, New_KNN_ind1 = KNN_Alg(Vision,1000)

#print(New_KNN_ind0)

Star 0 (array([[0.        , 0.29803175]]), array([[0, 3]]))
Star 1 (array([[0.        , 0.22858924]]), array([[1, 4]]))
Star 2 (array([[0.        , 0.24943533]]), array([[2, 6]]))
Star 3 (array([[0.        , 0.15773015]]), array([[3, 5]]))
Star 4 (array([[0.        , 0.22858924]]), array([[4, 1]]))
Star 5 (array([[0.       , 0.0762357]]), array([[5, 7]]))
Star 6 (array([[0.        , 0.04557604]]), array([[6, 7]]))
Star 7 (array([[0.        , 0.04557604]]), array([[7, 6]]))
Star 8 (array([[0.        , 0.14431144]]), array([[ 8, 11]]))
Star 9 (array([[0.        , 0.24207048]]), array([[ 9, 40]]))
Star 10 (array([[0.        , 0.18753476]]), array([[10, 24]]))
Star 11 (array([[0.        , 0.14431144]]), array([[11,  8]]))
Star 12 (array([[0.        , 0.15184959]]), array([[12, 23]]))
Star 13 (array([[0.        , 0.20155182]]), array([[13, 22]]))
Star 14 (array([[0.        , 0.02499495]]), array([[14, 15]]))
Star 15 (array([[0.        , 0.02499495]]), array([[15, 14]]))
Star 16 (array([[0. 

In [9]:
#SINGLE STARS

#The initial indices in Vision are the natural numbers from 1 to 3117. Since we're working with array/list the 1st index is not 1 but 0. 
#So we define the initial indices as the natural numbers from 0 to 3116
init_vision_ind = np.linspace(0,3116, num=3117, dtype=int)
#Arrays contain the indices and the coord. RA,DEC of the Single Stars, correctly resized
single_star_ind, single_star_coord = single_star(init_vision_ind, New_KNN_ind0, New_KNN_ind1, Vision) 

In [10]:
#BINARY SYSTEM --> New Stars

new_star_coord, new_star_ind = coord_new_star(Vision, New_KNN_ind0, New_KNN_ind1)
#print(new_star_ind)

In [11]:
#Calculation of MF and CF
#At the end of step0 I can only have single or double systems --> t,q,f etc. = 0
MF_0 = frequency(len(single_star_ind), len(new_star_ind), 0, 0, 0, 0, 0, 0)
CF_0 = companion_fraction(len(single_star_ind), len(new_star_ind), 0, 0, 0, 0, 0, 0)
print(MF_0, CF_0)

0.00128493414712496 0.00128493414712496


In [12]:
#We need to put together all the info above 
#NOTE: when we have something like [number, nan] for the index it means we're considering a single star (number=index of the star in Vision)
#when we have [number,number] for the index it means we're considering a BS (numbers=indices of the Stars in Vision)
#In the first case (RA,DEC) are the coord of the Single Star shown in Vision
#In the second case (RA,DEC) are the coord of the New Star, i.e. the middle point

Vision1 = np.concatenate((single_star_coord, new_star_coord))
Indices1 = np.concatenate((single_star_ind, new_star_ind))
#print(Indices1)

In [13]:
#List1 contains the YSO surface densities for each star in VisionIII catalogue, List2 contains the distances of the 11-th neighbors
surface_density_YSO_1, R_10_1 = surface_density(Vision1) 
#density = [#obj / pc^2], R_10 = [pc]
print(surface_density_YSO_1)
print(R_10_1)
mean_1 = 0
for i in range(len(surface_density_YSO_1)):
  mean_1 += surface_density_YSO_1[i]
mean_surface_density_1 = mean_1/(len(surface_density_YSO_1)) #This value represents the mean value of the surface density

print(mean_surface_density_1)

Output streaming troncato alle ultime 5000 righe.
        0.01935058, 0.01995336, 0.02068703, 0.02458581, 0.03036318,
        0.03114733]]), array([[1447, 1551, 1516, 1388, 1283, 1290, 1555, 1399, 1335, 1456, 1400]]))
Star 1448 (array([[0.        , 0.01979655, 0.02101265, 0.02206404, 0.02224523,
        0.02670552, 0.02872595, 0.02886449, 0.02892554, 0.03010233,
        0.03238417]]), array([[1448, 1301, 1554, 1295, 1279, 1235, 1355, 1619, 1583, 1215, 1639]]))
Star 1449 (array([[0.        , 0.01513918, 0.01696763, 0.01871623, 0.02112926,
        0.02344705, 0.02563576, 0.03214779, 0.03531648, 0.0394754 ,
        0.03980357]]), array([[1449, 1325, 1311, 1371, 1326, 1239, 1634, 1130, 1163, 1692, 1345]]))
Star 1450 (array([[0.        , 0.0144184 , 0.0202191 , 0.02187426, 0.04212677,
        0.04254185, 0.0568295 , 0.05812978, 0.05842562, 0.06827038,
        0.07284664]]), array([[1450, 1319, 1346, 1525, 1488, 1683, 1000,  994, 1570, 1052, 1791]]))
Star 1451 (array([[0.        , 0.00307611

In [14]:
#STEP 1
Sep_AU_step1 = []
KNN_ind0_step1 = []
KNN_ind1_step1 = []
Sep_AU_step1, KNN_ind0_step1, KNN_ind1_step1 = KNN_Alg(Vision1, 3000)

#KNN_ind0_step1 contains the indices of the Central Star in Vision1
#KNN_ind1_step1 contains the indices of the Nearest Neighbor in Vision1

Star 0 (array([[0.        , 0.29803175]]), array([[0, 3]]))
Star 1 (array([[0.        , 0.22858924]]), array([[1, 4]]))
Star 2 (array([[0.        , 0.24943533]]), array([[2, 6]]))
Star 3 (array([[0.        , 0.15773015]]), array([[3, 5]]))
Star 4 (array([[0.        , 0.22858924]]), array([[4, 1]]))
Star 5 (array([[0.       , 0.0762357]]), array([[5, 7]]))
Star 6 (array([[0.        , 0.04557604]]), array([[6, 7]]))
Star 7 (array([[0.        , 0.04557604]]), array([[7, 6]]))
Star 8 (array([[0.        , 0.14431144]]), array([[ 8, 11]]))
Star 9 (array([[0.        , 0.24207048]]), array([[ 9, 40]]))
Star 10 (array([[0.        , 0.18753476]]), array([[10, 24]]))
Star 11 (array([[0.        , 0.14431144]]), array([[11,  8]]))
Star 12 (array([[0.        , 0.15184959]]), array([[12, 23]]))
Star 13 (array([[0.        , 0.20155182]]), array([[13, 22]]))
Star 14 (array([[0.        , 0.02499495]]), array([[14, 15]]))
Star 15 (array([[0.        , 0.02499495]]), array([[15, 14]]))
Star 16 (array([[0. 

In [15]:
#STEP 1 --> we use KNN for the second time 

#Single Stars (step 1)
vision1_ind = np.linspace(0,3112, num=3113, dtype=int)
single_star_ind1, single_star_coord1 = single_star(vision1_ind, KNN_ind0_step1, KNN_ind1_step1, Vision1) 
#print(single_star_ind1)
#print(len(single_star_ind1))
#New Stars (step 1)
new_star_coord1, new_star_ind1 = coord_new_star(Vision1, KNN_ind0_step1, KNN_ind1_step1)
#print(new_star_ind)
#print(len(new_star_ind))

single1_vision = []
for i in range(len(single_star_ind1)):
  single1_vision.append(Indices1[int(single_star_ind1[i][0])][0])
  single1_vision.append(Indices1[int(single_star_ind1[i][0])][1])

single1_vision = np.reshape(single1_vision, (len(single_star_ind1),2))

newstar1_vision = []
for i in range(len(new_star_ind1)):
  newstar1_vision.append(Indices1[int(new_star_ind1[i][0])])
  newstar1_vision.append(Indices1[int(new_star_ind1[i][1])])

newstar1_vision = np.reshape(newstar1_vision, (len(new_star_ind1),4))

In [16]:
#We need to put together all the info above
#CATALOGUE
Vision2 = np.concatenate((single_star_coord1, new_star_coord1))

#INDICES IN VISION FOR ALL THE OBJECTS IN THE CATALOGUE ABOVE
#single1_vision and newstar1_vision do not have the same shape. We need to reshape single1_vision
single1_vision_reshape = []
for i in range(len(single1_vision)):
  single1_vision_reshape.append(single1_vision[i][0])
  single1_vision_reshape.append(single1_vision[i][1])
  single1_vision_reshape.append('NaN')
  single1_vision_reshape.append('NaN')

single1_vision_reshape = np.reshape(single1_vision_reshape, (len(single1_vision),4))
#print(single1_vision_reshape)
Indices2 = np.concatenate((single1_vision_reshape, newstar1_vision))
#print(Indices2)

In [17]:
#Calculation of MF and CF
#At the end of step1 I have: (I) single star, (II) BS, (III) ST
#(I) The star (which is a single star in the step0) cannot find a companion --> The index (in Indices2) contains 3 NaN
#(II) One single star (in step0) match with anothe Single star or a BS (step0) cannot find a companion --> The index contains 2 NaN
#(III) One single star + BS or viceversa --> the index contains 1 NaN 

#We need to compute s e b
binary_step1_vision = []
triple_step1_vision = []
s = 0 #Sinle Star
b = 0 #Binary System
t = 0 #Triple System

c = 0 #counter
for i in range(len(Indices2)):
  for j in range(0,4):
    if Indices2[i][j]=='NaN':
      c=c+1
  if c==1:
    t = t+1
    triple_step1_vision.append(Indices2[i])
  else: 
    if c==2:
      b = b+1
      binary_step1_vision.append(Indices2[i])
    else:
      s = s+1
  c = 0

binary_step1_vision = np.array(binary_step1_vision)
triple_step1_vision = np.array(triple_step1_vision)
print(triple_step1_vision)
print(s,b,t)
MF_1 = frequency(s, b, t, 0, 0, 0, 0, 0)
CF_1 = companion_fraction(s, b, t, 0, 0, 0, 0, 0)
print(MF_1, CF_1)

[['2859' 'NaN' '2683' '2858']]
2876 122 1
0.04101367122374125 0.041347115705235075


In [18]:
surface_density_YSO_2, R_10_2 = surface_density(Vision2) 
#density = [#obj / pc^2], R_10 = [pc]
print(surface_density_YSO_2)
print(R_10_2)
mean_2 = 0
for i in range(len(surface_density_YSO_2)):
  mean_2 += surface_density_YSO_2[i]
mean_surface_density_2 = mean_2/(len(surface_density_YSO_2)) #This value represents the mean value of the surface density

print(mean_surface_density_2)

Output streaming troncato alle ultime 5000 righe.
        0.01088823, 0.01144466, 0.01167577, 0.01284359, 0.01317953,
        0.01349363]]), array([[1333, 1341, 1309, 1338, 1280, 1277, 1296, 1253, 1236, 1344, 1269]]))
Star 1334 (array([[0.        , 0.00468429, 0.00887423, 0.02130654, 0.02560505,
        0.02623223, 0.03303024, 0.03705094, 0.04210549, 0.0429716 ,
        0.04716756]]), array([[1334, 1312, 1264, 2957, 1431, 1197, 1311, 1049, 1361, 1443,  935]]))
Star 1335 (array([[0.        , 0.01099409, 0.01225587, 0.01882253, 0.03373813,
        0.04730997, 0.05090419, 0.05344532, 0.05999541, 0.06091473,
        0.06239201]]), array([[1335, 1367, 1400, 2945, 1521, 1229,  953,  997,  912, 1604, 1612]]))
Star 1336 (array([[0.        , 0.00958997, 0.01049236, 0.01836119, 0.01957652,
        0.02762747, 0.02778228, 0.03703698, 0.03756449, 0.0377875 ,
        0.04060012]]), array([[1336, 1343, 1315, 1217, 1249, 1502, 1491, 1172, 1377, 1137, 1007]]))
Star 1337 (array([[0.        , 0.00718461

In [19]:
#STEP 2 --> we use KNN for the third time 

Sep_AU_step2 = []
KNN_ind0_step2 = []
KNN_ind1_step2 = []
Sep_AU_step2, KNN_ind0_step2, KNN_ind1_step2 = KNN_Alg(Vision2, 5000)

#KNN_ind0_step2 contains the indices of the Central Star in Vision2
#KNN_ind1_step2 contains the indices of the Nearest Neighbor in Vision2

Star 0 (array([[0.        , 0.29803175]]), array([[0, 3]]))
Star 1 (array([[0.        , 0.22858924]]), array([[1, 4]]))
Star 2 (array([[0.        , 0.24943533]]), array([[2, 6]]))
Star 3 (array([[0.        , 0.15773015]]), array([[3, 5]]))
Star 4 (array([[0.        , 0.22858924]]), array([[4, 1]]))
Star 5 (array([[0.       , 0.0762357]]), array([[5, 7]]))
Star 6 (array([[0.        , 0.04557604]]), array([[6, 7]]))
Star 7 (array([[0.        , 0.04557604]]), array([[7, 6]]))
Star 8 (array([[0.        , 0.14431144]]), array([[ 8, 11]]))
Star 9 (array([[0.        , 0.24207048]]), array([[ 9, 35]]))
Star 10 (array([[0.        , 0.18753476]]), array([[10, 24]]))
Star 11 (array([[0.        , 0.14431144]]), array([[11,  8]]))
Star 12 (array([[0.        , 0.15184959]]), array([[12, 23]]))
Star 13 (array([[0.        , 0.20155182]]), array([[13, 22]]))
Star 14 (array([[0.        , 0.02499495]]), array([[14, 15]]))
Star 15 (array([[0.        , 0.02499495]]), array([[15, 14]]))
Star 16 (array([[0. 

In [20]:
#Single Stars (step 2)
vision2_ind = np.linspace(0,2998, num=2999, dtype=int)
single_star_ind2, single_star_coord2 = single_star(vision2_ind, KNN_ind0_step2, KNN_ind1_step2, Vision2) 
#print(single_star_ind2)
#print(len(single_star_ind2))

#New Stars (step 2)
new_star_coord2, new_star_ind2 = coord_new_star(Vision2, KNN_ind0_step2, KNN_ind1_step2)
#print(new_star_ind2)
#print(len(new_star_ind2))

In [21]:
#Single star indices in VISION
single2_vision = []
for i in range(len(single_star_ind2)):
  for j in range(0,4):
    single2_vision.append(Indices2[int(single_star_ind2[i][0])][j])

single2_vision = np.reshape(single2_vision, (len(single_star_ind2),4)) #Indices of the Single Star for the step2 in VISION
#print(single2_vision)

#New star indices in VISION
newstar2_vision = []
for i in range(len(new_star_ind2)):
  for j in range(0,4):
    newstar2_vision.append(Indices2[int(new_star_ind2[i][0])][j])
  for k in range(0,4):
    newstar2_vision.append(Indices2[int(new_star_ind2[i][1])][k])

newstar2_vision = np.reshape(newstar2_vision, (len(new_star_ind2),8))
#print(newstar2_vision)

In [22]:
#Let's reshape correclty the single2_vision Indices
single2_vision_reshape = []
for i in range(len(single2_vision)):
  single2_vision_reshape.append(single2_vision[i][0])
  single2_vision_reshape.append(single2_vision[i][1])
  single2_vision_reshape.append(single2_vision[i][2])
  single2_vision_reshape.append(single2_vision[i][3])
  single2_vision_reshape.append('NaN')
  single2_vision_reshape.append('NaN')
  single2_vision_reshape.append('NaN')
  single2_vision_reshape.append('NaN')

single2_vision_reshape = np.reshape(single2_vision_reshape, (len(single2_vision),8))
#print(single2_vision_reshape)

In [23]:
Vision3 = np.concatenate((single_star_coord2, new_star_coord2))
Indices3 = np.concatenate((single2_vision_reshape, newstar2_vision))

In [24]:
#Calculation of MF and CF
#At the end of step2 I have from single stars to systems with multiplicity 4

#We need to compute s,b,t and q
binary_step2_vision = []
triple_step2_vision = []
quadruple_step2_vision = []
s2 = 0 #Sinle Star
b2 = 0 #Binary System
t2 = 0 #Triple System
q2 = 0 #Quadruple System

count = 0 #counter
for i in range(len(Indices3)):
  for j in range(0,8):
    if Indices3[i][j]=='NaN':
      count=count+1
  if count==4:
    q2 = q2+1
    quadruple_step2_vision.append(Indices3[i])
  else:
    if count==5:
      t2 = t2+1
      triple_step2_vision.append(Indices3[i])
    else:
      if count==6:
        b2 = b2+1
        binary_step2_vision.append(Indices3[i])
      else:
        s2 = s2+1
  count = 0

binary_step2_vision = np.array(binary_step2_vision)
triple_step2_vision = np.array(triple_step2_vision)
quadruple_step2_vision = np.array(quadruple_step2_vision)
print(s2,b2,t2,q2)
MF_2 = frequency(s2,b2,t2,q2,0,0,0,0)
CF_2 = companion_fraction(s2,b2,t2,q2,0,0,0,0)
print(MF_2, CF_2)
#print(binary_step2_vision)

2575 240 24 7
0.09522136331693605 0.10857343640196768


In [25]:
surface_density_YSO_3, R_10_3 = surface_density(Vision3) 
#density = [#obj / pc^2], R_10 = [pc]
print(surface_density_YSO_3)
print(R_10_3)
mean_3 = 0
for i in range(len(surface_density_YSO_3)):
  mean_3 += surface_density_YSO_3[i]
mean_surface_density_3 = mean_3/(len(surface_density_YSO_3)) #This value represents the mean value of the surface density

print(mean_surface_density_3)

Output streaming troncato alle ultime 5000 righe.
        0.01576078, 0.01611468, 0.01664926, 0.016923  , 0.01734051,
        0.01877382]]), array([[1180, 1192, 1241, 1135, 1114, 1100, 1223, 1268, 1121, 2761, 1085]]))
Star 1181 (array([[0.        , 0.00374991, 0.00881911, 0.01216908, 0.01285056,
        0.01345357, 0.01441844, 0.01590668, 0.01770243, 0.01826719,
        0.02003701]]), array([[1181, 2630, 2771, 1230, 1152, 1127, 1179, 1098, 1103, 2770, 1082]]))
Star 1182 (array([[0.        , 0.00425664, 0.00494043, 0.00977164, 0.01144854,
        0.01359726, 0.01370325, 0.01482425, 0.01647072, 0.0167009 ,
        0.01681193]]), array([[1182, 1171, 1191, 1144, 2631, 1123, 2625, 1252, 1233, 2765, 1132]]))
Star 1183 (array([[0.        , 0.00353231, 0.00384884, 0.00815602, 0.010025  ,
        0.01061266, 0.01067852, 0.01341233, 0.01566865, 0.0176877 ,
        0.01797696]]), array([[1183, 1169, 1208, 2627, 1186, 1146, 1159, 1125, 1262, 1119, 1261]]))
Star 1184 (array([[0.        , 0.02187426

In [26]:
#STEP 3 --> we use KNN for the fourth time 

Sep_AU_step3 = []
KNN_ind0_step3 = []
KNN_ind1_step3 = []
Sep_AU_step3, KNN_ind0_step3, KNN_ind1_step3 = KNN_Alg(Vision3, 8000)

Star 0 (array([[0.        , 0.29803175]]), array([[0, 3]]))
Star 1 (array([[0.        , 0.22858924]]), array([[1, 4]]))
Star 2 (array([[0.        , 0.24943533]]), array([[2, 6]]))
Star 3 (array([[0.        , 0.15773015]]), array([[3, 5]]))
Star 4 (array([[0.        , 0.22858924]]), array([[4, 1]]))
Star 5 (array([[0.       , 0.0762357]]), array([[5, 7]]))
Star 6 (array([[0.        , 0.04557604]]), array([[6, 7]]))
Star 7 (array([[0.        , 0.04557604]]), array([[7, 6]]))
Star 8 (array([[0.        , 0.14431144]]), array([[ 8, 11]]))
Star 9 (array([[0.        , 0.24207048]]), array([[ 9, 35]]))
Star 10 (array([[0.        , 0.18753476]]), array([[10, 24]]))
Star 11 (array([[0.        , 0.14431144]]), array([[11,  8]]))
Star 12 (array([[0.        , 0.15184959]]), array([[12, 23]]))
Star 13 (array([[0.        , 0.20155182]]), array([[13, 22]]))
Star 14 (array([[0.        , 0.02499495]]), array([[14, 15]]))
Star 15 (array([[0.        , 0.02499495]]), array([[15, 14]]))
Star 16 (array([[0. 

In [27]:
#Single Stars (step 3) in Vision3
vision3_ind = np.linspace(0,2845, num=2846, dtype=int)
single_star_ind3, single_star_coord3 = single_star(vision3_ind, KNN_ind0_step3, KNN_ind1_step3, Vision3) 
#print(single_star_ind3)
#print(len(single_star_ind3))

#New Stars (step 3) in Vision3
new_star_coord3, new_star_ind3 = coord_new_star(Vision3, KNN_ind0_step3, KNN_ind1_step3)
#print(new_star_ind3)
#print(len(new_star_ind3))

In [28]:
#Single star indices in VISION
single3_vision = []
for i in range(len(single_star_ind3)):
  for j in range(0,8):
    single3_vision.append(Indices3[int(single_star_ind3[i][0])][j])

single3_vision = np.reshape(single3_vision, (len(single_star_ind3),8)) #Indices of the Single Star for the step3 in VISION

#New star indices in VISION
newstar3_vision = []
for i in range(len(new_star_ind3)):
  for j in range(0,8):
    newstar3_vision.append(Indices3[int(new_star_ind3[i][0])][j])
  for k in range(0,8):
    newstar3_vision.append(Indices3[int(new_star_ind3[i][1])][k])


newstar3_vision = np.reshape(newstar3_vision, (len(new_star_ind3),16))
#print(newstar3_vision)

In [29]:
#Let's reshape correclty the single3_vision Indices
single3_vision_reshape = []
for i in range(len(single3_vision)):
  for j in range(0,8):
    single3_vision_reshape.append(single3_vision[i][j])
    single3_vision_reshape.append('NaN')

single3_vision_reshape = np.reshape(single3_vision_reshape, (len(single3_vision),16))
#print(single3_vision_reshape)

In [30]:
Vision4 = np.concatenate((single_star_coord3, new_star_coord3))
Indices4 = np.concatenate((single3_vision_reshape, newstar3_vision))

In [31]:
#Calculation of MF and CF
#At the end of step3 I have from single stars to systems with multiplicity 4

#We need to compute s,b,t and q
binary_step3_vision = []
triple_step3_vision = []
quadruple_step3_vision = []
five_step3_vision = []
six_step3_vision = []
seven_step3_vision = []
eight_step3_vision = []
ss = 0 #Sinle Star
sb = 0 #Binary System
st = 0 #Triple System
sq = 0 #Quadruple System
sf = 0 #multiplicity 5
ssis = 0 #multiplicity 6
ssev = 0 #multiplicity 7
se = 0 #multiplicity 8

g = 0 #counter
for i in range(len(Indices4)):
  for j in range(0,16):
    if Indices4[i][j]!='NaN':
      g = g+1
  if g==1:
    ss = ss+1
  else:
    if g==2:
      sb = sb+1
      binary_step3_vision.append(Indices4[i])
    else:
      if g==3:
        st = st+1
        triple_step3_vision.append(Indices4[i])
      else:
        if g==4:
          sq = sq+1
          quadruple_step3_vision.append(Indices4[i])
        else:
          if g==5:
            sf = sf+1
            five_step3_vision.append(Indices4[i])
          else: 
            if g==6:
              ssis = ssis+1
              six_step3_vision.append(Indices4[i])
            else:
              if g==7:
                ssev = ssev+1
                seven_step3_vision.append(Indices4[i])
              else:
                se = se+1
                eight_step3_vision.append(Indices4[i])
  g = 0

binary_step3_vision = np.array(binary_step3_vision)
triple_step3_vision = np.array(triple_step3_vision)
quadruple_step3_vision = np.array(quadruple_step3_vision)
five_step3_vision = np.array(five_step3_vision)
six_step3_vision = np.array(six_step3_vision)
seven_step3_vision = np.array(seven_step3_vision)
eight_step3_vision = np.array(eight_step3_vision)
print(ss,sb,st,sq,sf,ssis,ssev,se)
MF_3 = frequency(ss,sb,st,sq,sf,ssis,ssev,se)
CF_3 = companion_fraction(ss,sb,st,sq,sf,ssis,ssev,se)
print(MF_3, CF_3)

2195 328 67 37 9 5 2 1
0.16981845688350983 0.24697428139183056


In [32]:
surface_density_YSO_4, R_10_4 = surface_density(Vision4) 
#density = [#obj / pc^2], R_10 = [pc]
print(surface_density_YSO_4)
print(R_10_4)
mean_4 = 0
for i in range(len(surface_density_YSO_4)):
  mean_4 += surface_density_YSO_4[i]
mean_surface_density_4 = mean_4/(len(surface_density_YSO_4)) #This value represents the mean value of the surface density

print(mean_surface_density_4)

Output streaming troncato alle ultime 5000 righe.
        0.04131154, 0.04149988, 0.04442416, 0.04645515, 0.04699225,
        0.05047553]]), array([[ 978,  966,  941,  912, 1085,  842, 2519,  987, 2308,  933,  852]]))
Star 979 (array([[0.        , 0.01032465, 0.01213201, 0.0159499 , 0.02243748,
        0.02498521, 0.02627536, 0.02696169, 0.02941537, 0.03007804,
        0.03016975]]), array([[ 979, 2525, 1015, 1021,  906,  949, 1045,  923,  882,  928, 1067]]))
Star 980 (array([[0.        , 0.01738221, 0.02563576, 0.03565899, 0.03832388,
        0.0407617 , 0.0424864 , 0.04263949, 0.04786379, 0.04790408,
        0.04856316]]), array([[ 980, 1020,  896, 1077,  870, 2222,  849,  985,  998,  927,  816]]))
Star 981 (array([[0.        , 0.04073363, 0.05224686, 0.05576972, 0.07977272,
        0.09537152, 0.10444625, 0.10996429, 0.12552639, 0.12925619,
        0.13504184]]), array([[ 981, 1049, 1111, 1014, 1173,  673, 2523, 1234, 1226, 1199,  951]]))
Star 982 (array([[0.        , 0.01479551, 0.

In [33]:
#STEP 4 

Sep_AU_step4 = []
KNN_ind0_step4 = []
KNN_ind1_step4 = []
Sep_AU_step4, KNN_ind0_step4, KNN_ind1_step4 = KNN_Alg(Vision4, 10000)

Star 0 (array([[0.        , 0.29803175]]), array([[0, 3]]))
Star 1 (array([[0.        , 0.22858924]]), array([[1, 4]]))
Star 2 (array([[0.        , 0.24943533]]), array([[2, 6]]))
Star 3 (array([[0.        , 0.15773015]]), array([[3, 5]]))
Star 4 (array([[0.        , 0.22858924]]), array([[4, 1]]))
Star 5 (array([[0.       , 0.0762357]]), array([[5, 7]]))
Star 6 (array([[0.        , 0.04557604]]), array([[6, 7]]))
Star 7 (array([[0.        , 0.04557604]]), array([[7, 6]]))
Star 8 (array([[0.        , 0.14431144]]), array([[ 8, 11]]))
Star 9 (array([[0.        , 0.24207048]]), array([[ 9, 34]]))
Star 10 (array([[0.        , 0.18753476]]), array([[10, 24]]))
Star 11 (array([[0.        , 0.14431144]]), array([[11,  8]]))
Star 12 (array([[0.        , 0.15184959]]), array([[12, 23]]))
Star 13 (array([[0.        , 0.20155182]]), array([[13, 22]]))
Star 14 (array([[0.        , 0.02499495]]), array([[14, 15]]))
Star 15 (array([[0.        , 0.02499495]]), array([[15, 14]]))
Star 16 (array([[0. 

In [34]:
#Single Stars (step 4) in Vision4
vision4_ind = np.linspace(0,2643, num=2644, dtype=int)
single_star_ind4, single_star_coord4 = single_star(vision4_ind, KNN_ind0_step4, KNN_ind1_step4, Vision4) 
#print(single_star_ind4)
#print(len(single_star_ind4))

#New Stars (step 4) in Vision4
new_star_coord4, new_star_ind4 = coord_new_star(Vision4, KNN_ind0_step4, KNN_ind1_step4)
#print(new_star_ind4)
#print(len(new_star_ind4))

In [35]:
#Single star indices in VISION
single4_vision = []
for i in range(len(single_star_ind4)):
  for j in range(0,16):
    single4_vision.append(Indices4[int(single_star_ind4[i][0])][j])

single4_vision = np.reshape(single4_vision, (len(single_star_ind4),16)) #Indices of the Single Star for the step4 in VISION

#New star indices in VISION
newstar4_vision = []
for i in range(len(new_star_ind4)):
  for j in range(0,16):
    newstar4_vision.append(Indices4[int(new_star_ind4[i][0])][j])
  for k in range(0,16):
    newstar4_vision.append(Indices4[int(new_star_ind4[i][1])][k])


newstar4_vision = np.reshape(newstar4_vision, (len(new_star_ind4),32))
#print(newstar4_vision)

In [36]:
#Let's reshape correclty the single4_vision Indices
single4_vision_reshape = []
for i in range(len(single4_vision)):
  for j in range(0,16):
    single4_vision_reshape.append(single4_vision[i][j])
    single4_vision_reshape.append('NaN')

single4_vision_reshape = np.reshape(single4_vision_reshape, (len(single4_vision),32))
#print(single4_vision_reshape)

In [37]:
Vision5 = np.concatenate((single_star_coord4, new_star_coord4))
Indices5 = np.concatenate((single4_vision_reshape, newstar4_vision))

In [38]:
#Calculation of MF and CF
#At the end of step4 I have from single stars to systems with multiplicity 4

#We need to compute s,b,t and q
s1 = 0 #Sinle Star
b1 = 0 #Binary System
t1 = 0 #Triple System
q1 = 0 #Quadruple System
sf1 = 0 #multiplicity 5
ssis1 = 0 #multiplicity 6
ssev1 = 0 #multiplicity 7
se1 = 0 #multiplicity 8
n1 = 0 #multiplicity 9
st1 = 0 #multiplicity 10
tt1 = 0 #multiplicity 11

t = 0 #counter
for i in range(len(Indices5)):
  for j in range(0,32):
    if Indices5[i][j]!='NaN':
      t = t+1
  if t==1:
    s1 = s1+1
  else:
    if t==2:
      b1 = b1+1
    else:
      if t==3:
        t1 = t1+1
      else:
        if t==4:
          q1 = q1+1
        else:
          if t==5:
            sf1 = sf1+1
          else: 
            if t==6:
              ssis1 = ssis1+1
            else:
              if t==7:
                ssev1 = ssev1+1
              else:
                if t==8:
                  se1 = se1+1
                else:
                  if t==9:
                    n1 = n1+1
                  else:
                    if t==10:
                      st1 = st1+1
                    else:
                      tt1 = tt1+1
            
  t = 0

print(s1,b1,t1,q1,sf1,ssis1,ssev1,se1,n1,st1,tt1)

MF_4 = (b1+t1+q1+sf1+ssis1+ssev1+se1+n1+st1+tt1)/(s1+b1+t1+q1+sf1+ssis1+ssev1+se1+n1+st1+tt1)
CF_4 = (b1+2*t1+3*q1+4*sf1+5*ssis1+6*ssev1+7*se1+8*n1+9*st1+10*tt1)/(s1+b1+t1+q1+sf1+ssis1+ssev1+se1+n1+st1+tt1)
print(MF_4, CF_4)

1978 297 72 53 20 12 12 11 4 2 6
0.1982164572355087 0.4049452776651804


In [39]:
#STEP 0 --> d = 1000AU = 0.00484814 parsec
#new_star_ind[i][0] is for the first star in the BS, new_star_ind[i][1] for the 2nd one
probability_comp_1 = []
probability_comp_2 = []
for i in range(len(new_star_ind)):
  #I'm considering the density around the 1st star
  probability_comp_1.append(comp_prob(surface_density_YSO[new_star_ind[i][0]], 0.00484814))
  #I'm considering the density around the 2nd star
  probability_comp_2.append(comp_prob(surface_density_YSO[new_star_ind[i][1]], 0.00484814))

#Let's try with the mean surface density for the multiple system 
mean_density = []
probability_comp_mean = []
pair_step0 = []
for i in range(len(new_star_ind)):
  mean_density.append((surface_density_YSO[new_star_ind[i][0]]+surface_density_YSO[new_star_ind[i][1]])/2)
  probability_comp_mean.append(comp_prob(mean_density[i], 0.00484814))
  pair_step0.append(new_star_ind[i])

print(probability_comp_1)
print(probability_comp_2)
print(probability_comp_mean)
print(new_star_ind)
print(pair_step0)

[0.9963302756691965, 0.9927842331657439, 0.9892355072822961, 0.9989300063891621]
[0.9962876307608673, 0.992847190982252, 0.989708013791983, 0.9989105880478488]
[0.9963089529868662, 0.9928157115749519, 0.9894717323323926, 0.9989202971713205]
[[ 761  765]
 [ 767  770]
 [ 893  897]
 [2683 2858]]
[array([761, 765]), array([767, 770]), array([893, 897]), array([2683, 2858])]


In [40]:
#STEP 1 --> d = 3000 AU = 0.01454441 parsec

prob_comp1_step1 = []
prob_comp2_step1 = []
for i in range(len(KNN_ind0_step1)):
  #I'm considering the density around the 1st star
  prob_comp1_step1.append(comp_prob(surface_density_YSO_1[KNN_ind0_step1[i]], 0.00484814))
  #I'm considering the density around the 2nd star
  prob_comp2_step1.append(comp_prob(surface_density_YSO_1[KNN_ind1_step1[i]], 0.00484814))

#Let's try with the mean surface density for the multiple system 
mean_density_step1 = []
prob_comp_mean_step1 = []
#pair_step1_visI = []
pair_step1_vis = []
for i in range(len(KNN_ind0_step1)):
  mean_density_step1.append((surface_density_YSO_1[KNN_ind0_step1[i]]+surface_density_YSO_1[KNN_ind1_step1[i]])/2)
  prob_comp_mean_step1.append(comp_prob(mean_density_step1[i], 0.00484814))
  #pair_step1_visI.append(KNN_ind0_step1[i])
  #pair_step1_visI.append(KNN_ind1_step1[i])
  pair_step1_vis.append(Indices1[new_star_ind1[i][0]]) #Index in Vision of the 1st star 
  pair_step1_vis.append(Indices1[new_star_ind1[i][1]]) #Index in Vision of the 2nd star

pair_step1_vis_res = np.reshape(pair_step1_vis, (120,4))
#pair_step1_vis = np.reshape(pair_step1_vis,(len(KNN_ind0_step1),2))
print(prob_comp1_step1)
print(prob_comp2_step1)
print(min(prob_comp_mean_step1))
#print(pair_step1_vis)

#Let's check the systems with multiplicity > 2
#At step 1, only one triple system was found [['2859' 'NaN' '2683' '2858']] (i.e. single star+BS)
AB = comp_prob(surface_density_YSO[2859], 0.00484814)
for i in range(len(pair_step0)):
  if int(triple_step1_vision[0][2])==int(pair_step0[i][0]):
    CD = probability_comp_mean[i]

for i in range(len(pair_step1_vis_res)):
  if int(triple_step1_vision[0][0])==int(pair_step1_vis_res[i][0]):
    ABCD = prob_comp_mean_step1[i]

print(AB, CD, ABCD)
N = 1+AB+ABCD+(CD*ABCD) #Should I consider AB?
print(N)
#print(pair_step1_vis_res)

[0.996894320892919, 0.9962522223973879, 0.9963430805392232, 0.9986311060979447, 0.9983931470953015, 0.9988219899612635, 0.9969135395025249, 0.9969225734233632, 0.9941419003950791, 0.9925015068444408, 0.9934902769908074, 0.9971147921420696, 0.9927692362648288, 0.9701039400744065, 0.995676860208649, 0.9904608360946416, 0.9648879851580457, 0.94834023135859, 0.9924113200354964, 0.962625793741251, 0.9939149621500468, 0.9519353262177066, 0.9745893211248101, 0.9546551043050124, 0.9473375811396054, 0.9701264059320667, 0.9423428984315131, 0.959216429220561, 0.9864386236644368, 0.975058603162243, 0.9775462325680909, 0.9347388490850054, 0.9935943739789412, 0.9589896053098268, 0.9622960389587044, 0.9989911501421078, 0.9958844275597464, 0.9444565516925821, 0.9106603016115893, 0.9443168817461872, 0.8950246752023129, 0.9420004773626551, 0.945345690135448, 0.9598730113763815, 0.9219308724013957, 0.9449544202313629, 0.9618392552329872, 0.9681710856567648, 0.9659214372823661, 0.9521956950188879, 0.97255

In [41]:
#STEP 2 --> d = 5000 AU = 0.02424068 parsec

prob_comp1_step2 = []
prob_comp2_step2 = []
for i in range(len(KNN_ind0_step2)):
  #I'm considering the density around the 1st star
  prob_comp1_step2.append(comp_prob(surface_density_YSO_2[KNN_ind0_step2[i]], 0.02424068))
  #I'm considering the density around the 2nd star
  prob_comp2_step2.append(comp_prob(surface_density_YSO_2[KNN_ind1_step2[i]], 0.02424068))

#Let's try with the mean surface density for the multiple system 
mean_density_step2 = []
prob_comp_mean_step2 = []
pair_step2_vis = []
prob_comp_mean_step2_corr = []
for i in range(len(KNN_ind0_step2)):
  mean_density_step2.append((surface_density_YSO_2[KNN_ind0_step2[i]]+surface_density_YSO_2[KNN_ind1_step2[i]])/2)
  prob_comp_mean_step2.append(comp_prob(mean_density_step2[i], 0.02424068)) 
  #If the probability is too small, the multiple system is not considered as such
  if prob_comp_mean_step2[i]<0.5:
    pair_step2_vis.append(Indices2[new_star_ind2[i][0]]) #Index in Vision of the 1st star
    pair_step2_vis.append(Indices2[new_star_ind2[i][1]]) #Index in Vision of the 2nd star
    prob_comp_mean_step2_corr.append(prob_comp_mean_step2[i])
pair_step2_vis_res = np.reshape(pair_step2_vis, (63, 8))
#print(pair_step2_vis_res)

#Let's see what triple and quadruple systems fulfil the condition we placed on the probability
triple_step2_vision_corr = []
quadruple_step2_vision_corr = []
for i in range(len(triple_step2_vision)):
  for j in range(len(pair_step2_vis_res)):
    if int(triple_step2_vision[i][0])==int(pair_step2_vis_res[j][0]):
      triple_step2_vision_corr.append(triple_step2_vision[i])
print(len(triple_step2_vision_corr))
for i in range(len(quadruple_step2_vision)):
  for j in range(len(pair_step2_vis_res)):
    if int(quadruple_step2_vision[i][0])==int(pair_step2_vis_res[j][0]):
      quadruple_step2_vision_corr.append(quadruple_step2_vision[i])
print(len(quadruple_step2_vision_corr))


#Let's check the systems with multiplicity > 2
#At STEP 2 we found: 24 triple systems and 7 quaruple systems
index_triple_step2 = []
prob_triple_corr = []
#TRIPLE SYSTEMS
prob_single = []
prob_triple_12 = []
prob_binary_12 = []
prob_triple_02 = []
prob_binary_02 = []
#Probability of each member belonging to the Triple System 
#1) Probability that the 1st star is a Single Star
for i in range(len(Indices1)):
  for j in range(len(triple_step2_vision_corr)):
    if int(Indices1[i][0])==int(triple_step2_vision[j][0]):
      prob_single.append(comp_prob(surface_density_YSO_1[i], 0.00484814))

#2) Intermediate probabilities
for i in range(len(triple_step2_vision_corr)):
  if triple_step2_vision_corr[i][5]!='NaN': #BS formed at step 0, TS formed at step 2
    #P_ST è stata calcolata in questo step, dunque è contenuta nella lista prob_comp_mean_step2[:] --> pair_step2_vis[j]=triple_step2_vision[i][0]
    for j in range(len(pair_step2_vis_res)):
      if int(pair_step2_vis_res[j][0])==int(triple_step2_vision_corr[i][0]):
        prob_triple_02.append(prob_comp_mean_step2[j])
    #P_SB è stata calcolata allo step 0, dunque è contenuta nella lista probability_comp_mean[:] --> pair_step0[k][0]=triple_step2_vision[i][4]
    for k in range(len(pair_step0)):
      if int(pair_step0[k][0])==int(triple_step2_vision_corr[i][4]):
        prob_binary_02.append(probability_comp_mean[k])
  elif triple_step2_vision_corr[i][6]!='NaN':
    #P_ST è stata calcolata in questo step, dunque è contenuta nella lista prob_comp_mean_step2[:] --> pair_step2_vis[j]=triple_step2_vision[i][0]
    for j in range(len(pair_step2_vis_res)):
      if int(pair_step2_vis_res[j][0])==int(triple_step2_vision_corr[i][0]):
        prob_triple_12.append(prob_comp_mean_step2[j])
    #P_SB è stata calcolata allo step 1, dunque è contenuta nella lista prob_comp_mean_step1[:] --> pair_step1_vis[g]=triple_step2_vision[i][4]
    for k in range(len(pair_step1_vis_res)):
      if int(pair_step1_vis_res[k][0])==int(triple_step2_vision_corr[i][4]):
        prob_binary_12.append(prob_comp_mean_step1[k])

#Let's compute the multiplicity N
# Single star + BS formed at step 1
N_12 = []
mult = 0
new_mult = 0
for i in range(len(prob_triple_12)):
  mult = 1+prob_single[i]+prob_triple_12[i]+(prob_triple_12[i]*prob_binary_12[i])
  N_12.append(mult)
  if N_12[i]<3:
    print("Probability of forming a TS", prob_triple_12[i])
    #new_mult = N_12[i]-prob_triple_12[i]
    #print("Nuova molteplicità", new_mult)
    print("Probability that the 1st member belongs to the system", prob_single[i])
    print("Probability that the 2nd member belongs to the system", prob_triple_12[i])
    print("Probability that the 3rd member belongs to the system", (prob_binary_12[i]*prob_triple_12[i]))
  else: 
    prob_triple_corr.append(prob_binary_12[i])
    index_triple_step2.append(triple_step2_vision_corr[i])


#Quadruple Systems
P12 = []
P34 = []
P1234 = []
for i in range(len(quadruple_step2_vision_corr)):
  for j in range(len(pair_step1_vis_res)):
    if int(quadruple_step2_vision_corr[i][0])==int(pair_step1_vis_res[j][0]):
      P12.append(prob_comp_mean_step1[j])
    elif int(quadruple_step2_vision_corr[i][4])==int(pair_step1_vis_res[j][0]):
      P34.append(prob_comp_mean_step1[j])

for i in range(len(quadruple_step2_vision_corr)):
  for j in range(len(pair_step2_vis_res)):
    if int(quadruple_step2_vision_corr[i][0])==int(pair_step2_vis_res[j][0]):
      P1234.append(prob_comp_mean_step2[j])

N_Q = []
mult1 = 0
for i in range(len(P12)):
  mult1 = 1+P12[i]+P1234[i]+(P34[i]*P1234[i])
  N_Q.append(mult1)
  if N_Q[i]<4:
    print("Probability of forming a QS", P1234[i])
    print("Probability that the 1st member belongs to the system", '1')
    print("Probability that the 2nd member belongs to the system", P12[i])
    print("Probability that the 3rd member belongs to the system", P34[i])
    print("Probability that the 4th member belongs to the system", (P34[i]*P1234[i]))
prob_triple_corr.append(P1234[2])
index_triple_step2.append(quadruple_step2_vision_corr[2])
index_triple_step2[3][2]='NaN'
index_triple_step2 = np.reshape(index_triple_step2, (4, 8))

print(prob_comp1_step2)
print(prob_comp2_step2)
print(prob_comp_mean_step2)
print(min(prob_comp_mean_step2))
#print(low_prob)
#print(N_02)
print(N_12)
print(min(N_12))
#print(len(P12), P12)
#print(len(P34), P34)
#print(len(P1234), P1234)
print(N_Q)
#print(prob_triple_corr)
print(index_triple_step2)

10
4
Probability of forming a TS 0.49952358698760085
Probability that the 1st member belongs to the system 0.9474639895965237
Probability that the 2nd member belongs to the system 0.49952358698760085
Probability that the 3rd member belongs to the system 0.4597993807517771
Probability of forming a TS 0.47060987668975685
Probability that the 1st member belongs to the system 0.9710590468875173
Probability that the 2nd member belongs to the system 0.47060987668975685
Probability that the 3rd member belongs to the system 0.4525475791196259
Probability of forming a TS 0.5011263811690885
Probability that the 1st member belongs to the system 0.9932955563873224
Probability that the 2nd member belongs to the system 0.5011263811690885
Probability that the 3rd member belongs to the system 0.47572718146598525
Probability of forming a TS 0.20521485057707947
Probability that the 1st member belongs to the system 0.8950246752023129
Probability that the 2nd member belongs to the system 0.205214850577079

In [42]:
#STEP 3 --> d = 8000 AU = 0.03878509 parsec

prob_comp1_step3 = []
prob_comp2_step3 = []
for i in range(len(KNN_ind0_step3)):
  #I'm considering the density around the 1st star
  prob_comp1_step3.append(comp_prob(surface_density_YSO_3[KNN_ind0_step3[i]], 0.03878509))
  #I'm considering the density around the 2nd star
  prob_comp2_step3.append(comp_prob(surface_density_YSO_3[KNN_ind1_step3[i]], 0.03878509))

#Let's try with the mean surface density for the multiple system 
mean_density_step3 = []
prob_comp_mean_step3 = []
pair_step3_vis = []
prob_comp_mean_step3_corr = []
for i in range(len(KNN_ind0_step3)):
  mean_density_step3.append((surface_density_YSO_3[KNN_ind0_step3[i]]+surface_density_YSO_3[KNN_ind1_step3[i]])/2)
  prob_comp_mean_step3.append(comp_prob(mean_density_step3[i], 0.03878509))
  if prob_comp_mean_step3[i]>0.9:
    pair_step3_vis.append(Indices3[new_star_ind3[i][0]])
    pair_step3_vis.append(Indices3[new_star_ind3[i][1]])
    prob_comp_mean_step3_corr.append(prob_comp_mean_step3[i])

pair_step3_vis_res = np.reshape(pair_step3_vis, (19,16))

'''
#Let's check the systems with multiplicity > 2
#At STEP 3 we found: 67 TS, 37 QS, 9 systems with multiplicity 5, 5 with moltiplicity 6, 2 with mult 7, 1 with mult 8

#TRIPLE SYSTEM 
#1) Probability that one star is a Single Star (at this step)
prob_single_step3 = []
for i in range(len(Indices2)):
  for j in range(1,len(triple_step3_vision)):
    if triple_step3_vision[j][10]!='NaN' or triple_step3_vision[j][12]!='NaN': #I'm considering the cases b) and c) --> Index of single star is in position 0
      if int(Indices2[i][0])==int(triple_step3_vision[j][0]):
        prob_single_step3.append(comp_prob(surface_density_YSO_2[i], 0.02424068))
    else: #Cases d) and e) --> Index of single star is in position 8
      if int(Indices2[i][0])==int(triple_step3_vision[j][8]):
        prob_single_step3.append(comp_prob(surface_density_YSO_2[i], 0.02424068))

#Intermediate probabilities
prob_binary_step1 = []
for i in range(1,len(triple_step3_vision)):
  for j in range(len(pair_step1_vis)):
    if triple_step3_vision[i][10]!='NaN': #Case b)
      if int(triple_step3_vision[i][8])==int(pair_step1_vis[j]):
        prob_binary_step1.append(prob_comp_mean_step1[j])
    elif triple_step3_vision[i][2]!='NaN': #Case e)
      if int(triple_step3_vision[i][0])==int(pair_step1_vis[j]):
        prob_binary_step1.append(prob_comp_mean_step1[j])
      
prob_binary_step2 = []
for i in range(1,len(triple_step3_vision)):
  for j in range(len(pair_step2_vis)):
    if triple_step3_vision[i][12]!='NaN': #Case c)
      if int(triple_step3_vision[i][8])==int(pair_step2_vis[j]):
        prob_binary_step2.append(prob_comp_mean_step2[j])
    elif triple_step3_vision[i][4]!='NaN': #Case d)
      if int(triple_step3_vision[i][0])==int(pair_step2_vis[j]):
        prob_binary_step2.append(prob_comp_mean_step2[j])

prob_binary_step3 = np.concatenate((prob_binary_step1, prob_binary_step2))
'''

print(prob_comp1_step3)
print(prob_comp2_step3)
print(prob_comp_mean_step3)
print(min(prob_comp_mean_step3))
#print(len(prob_single_step3), prob_single_step3)
#print(len(prob_binary_step1), prob_binary_step1)
#print(len(prob_binary_step2), prob_binary_step2)
#print(len(prob_binary_step3), prob_binary_step3)

[0.912874152091728, 0.8840777918679542, 0.9274331899043278, 0.9135587839553019, 0.8801612669305854, 0.7956716225618885, 0.7963110253277981, 0.4837901954671501, 0.7955709118716924, 0.7978900968913738, 0.7008401853625619, 0.7777819975791966, 0.7506059574021555, 0.7935232331272131, 0.1947965098530539, 0.8142544583589438, 0.7521895121421653, 0.7204878571522619, 0.4261244493908558, 0.40746003016636523, 0.694398437811159, 0.5158004584641959, 0.7231063582839394, 0.39855348009914127, 0.6407351619539285, 0.26814166453233185, 0.7173593833223562, 0.6913701823475111, 0.7122708375802902, 0.8219671588188568, 0.3630074271480168, 0.4337064793942895, 0.7067887690475287, 0.370915560176594, 0.2732149293520127, 0.20749616227313197, 0.24454675695330774, 0.4726983050742058, 0.4977300921950569, 0.30859571708636, 0.9607679002855158, 0.15006398425348297, 0.24649503488966265, 0.3304190149107858, 0.2483818891859355, 0.15990039367328637, 0.10955787480619283, 0.2505869265996052, 0.18157392794759653, 0.302541078768

In [43]:
#STEP 4 --> d = 10000 AU = 0.04848137 parsec

prob_comp1_step4 = []
prob_comp2_step4 = []
for i in range(len(KNN_ind0_step4)):
  #I'm considering the density around the 1st star
  prob_comp1_step4.append(comp_prob(surface_density_YSO_4[KNN_ind0_step4[i]], 0.04848137))
  #I'm considering the density around the 2nd star
  prob_comp2_step4.append(comp_prob(surface_density_YSO_4[KNN_ind1_step4[i]], 0.04848137))

#Let's try with the mean surface density for the multiple system 
mean_density_step4 = []
prob_comp_mean_step4 = []
pair_step4_vis = []
prob_comp_mean_step4_corr = []
for i in range(len(KNN_ind0_step4)):
  mean_density_step4.append((surface_density_YSO_4[KNN_ind0_step4[i]]+surface_density_YSO_4[KNN_ind1_step4[i]])/2)
  prob_comp_mean_step4.append(comp_prob(mean_density_step4[i], 0.04848137))
  if prob_comp_mean_step4[i]>0.6:
    pair_step4_vis.append(Indices4[new_star_ind4[i][0]]) #1st star in BS formed at step 4
    pair_step4_vis.append(Indices4[new_star_ind4[i][1]]) #2nd star in BS formed at step 4
    prob_comp_mean_step4_corr.append(prob_comp_mean_step4[i])

pair_step4_vis_res = np.reshape(pair_step4_vis, (73, 32))
print(len(pair_step4_vis_res))

print(prob_comp1_step4)
print(prob_comp2_step4)
print(prob_comp_mean_step4)
print(min(prob_comp_mean_step4))
print(len(prob_comp_mean_step4_corr))
print(len(pair_step4_vis_res))

73
[0.8863770058115339, 0.9745141502976249, 0.640468464725161, 0.8624217248086864, 0.6521165063487988, 0.7065143133918776, 0.5999154186619475, 0.6546782008612408, 0.695923850624513, 0.8430358870355479, 0.5753112793852556, 0.7574749348251959, 0.8375113553888852, 0.8030390726584823, 0.5823976414451558, 0.4911893690349864, 0.8470391350615314, 0.6985832635820236, 0.845572358548801, 0.16056667036208683, 0.7381050731767368, 0.5191710671273407, 0.5981743172600622, 0.3370241402545319, 0.19822595882017452, 0.29407092367164095, 0.16455360396350918, 0.5701672060683785, 0.2537787410528754, 0.8254014425612944, 0.5933855804722247, 0.22451886413109146, 0.267764353168836, 0.2978143475247687, 0.5510488614180489, 0.20277312510352916, 0.5342463099001379, 0.7089587807748923, 0.46237837338994636, 0.5004336146434782, 0.43784788586555007, 0.31983682385251055, 0.4868588764776235, 0.18600216039217787, 0.2551615724413209, 0.3589368177564941, 0.6920199503580782, 0.28862848568967997, 0.32434725962141675, 0.465202

In [44]:
#Create a new table that is like the previous one but no longer counts equal pairs 
CF = [CF_0, CF_1, CF_2, CF_3, CF_4]
MF = [MF_0, MF_1, MF_2, MF_3, MF_4]
Sep_range = [1000, 3000, 5000, 8000, 10000]
single = [len(single_star_ind), s, s2, ss, s1]
binary = [len(new_star_ind), b, b2, sb, b1] 
triple = [0, 0, t2, st, t1] 
quadruple = [0, 0, q2, sq, q1]
five = [0, 0, 0, sf, sf1]
superior = [0, 0, 0, ssis+ssis1+ssev+ssev1+se+se1, n1+st1]


t = Table()
t['Separation considered [AU]']=np.zeros(5, dtype=int)
t['Single Star']=np.zeros(5, dtype=int)
t['Binary System']=np.zeros(5, dtype=int)
t['Triple System']=np.zeros(5, dtype=int)
t['Quadruple System']=np.zeros(5, dtype=int)
t['Multiplicity 5']=np.zeros(5, dtype=int)
t['Higher multiplicities']=np.zeros(5, dtype=int)
t['MF']=np.zeros(5, dtype=float)
t['CF']=np.zeros(5, dtype=float)
for i in range(len(t['Binary System'])):
  t['Separation considered [AU]'][i]=Sep_range[i]
  t['Single Star'][i]=single[i]
  t['Binary System'][i]=binary[i]
  t['Triple System'][i]=triple[i]
  t['Quadruple System'][i]=quadruple[i]
  t['Multiplicity 5'][i]=five[i]
  t['Higher multiplicities'][i]=superior[i]
  t['MF'][i]=MF[i]
  t['CF'][i]=CF[i]

print(t)


Separation considered [AU] Single Star ...          CF         
-------------------------- ----------- ... --------------------
                      1000        3109 ...  0.00128493414712496
                      3000        2876 ... 0.041347115705235075
                      5000        2575 ...  0.10857343640196768
                      8000        2195 ...  0.24697428139183056
                     10000        1978 ...   0.4049452776651804


In [45]:
CORRpair_step2_vis = []
CORRprob_comp_mean_step2 = []
for i in range(len(pair_step2_vis_res)):
  d=0
  for j in range(0,8):
    if pair_step2_vis_res[i][j]!='NaN':
      d=d+1
  if d==2:
    CORRpair_step2_vis.append(pair_step2_vis_res[i])
    CORRprob_comp_mean_step2.append(prob_comp_mean_step2_corr[i])

print(len(pair_step2_vis_res[0]))
print(len(CORRpair_step2_vis))
CORRpair_step2_vis = np.reshape(CORRpair_step2_vis, (len(CORRpair_step2_vis), 8))
print(CORRpair_step2_vis)

8
49
[['674' 'NaN' 'NaN' 'NaN' '680' 'NaN' 'NaN' 'NaN']
 ['678' 'NaN' 'NaN' 'NaN' '681' 'NaN' 'NaN' 'NaN']
 ['681' 'NaN' 'NaN' 'NaN' '690' 'NaN' 'NaN' 'NaN']
 ['686' 'NaN' 'NaN' 'NaN' '711' 'NaN' 'NaN' 'NaN']
 ['698' 'NaN' 'NaN' 'NaN' '678' 'NaN' 'NaN' 'NaN']
 ['773' 'NaN' 'NaN' 'NaN' '791' 'NaN' 'NaN' 'NaN']
 ['785' 'NaN' 'NaN' 'NaN' '805' 'NaN' 'NaN' 'NaN']
 ['815' 'NaN' 'NaN' 'NaN' '829' 'NaN' 'NaN' 'NaN']
 ['852' 'NaN' 'NaN' 'NaN' '829' 'NaN' 'NaN' 'NaN']
 ['900' 'NaN' 'NaN' 'NaN' '929' 'NaN' 'NaN' 'NaN']
 ['901' 'NaN' 'NaN' 'NaN' '922' 'NaN' 'NaN' 'NaN']
 ['912' 'NaN' 'NaN' 'NaN' '930' 'NaN' 'NaN' 'NaN']
 ['929' 'NaN' 'NaN' 'NaN' '930' 'NaN' 'NaN' 'NaN']
 ['944' 'NaN' 'NaN' 'NaN' '930' 'NaN' 'NaN' 'NaN']
 ['959' 'NaN' 'NaN' 'NaN' '930' 'NaN' 'NaN' 'NaN']
 ['983' 'NaN' 'NaN' 'NaN' '1013' 'NaN' 'NaN' 'NaN']
 ['1029' 'NaN' 'NaN' 'NaN' '1033' 'NaN' 'NaN' 'NaN']
 ['1037' 'NaN' 'NaN' 'NaN' '1046' 'NaN' 'NaN' 'NaN']
 ['1038' 'NaN' 'NaN' 'NaN' '1048' 'NaN' 'NaN' 'NaN']
 ['1074' 'NaN' 'NaN

In [46]:
from tabulate import tabulate
probability_comp_mean = np.reshape(probability_comp_mean, (4,1))
info = {'Binary System': [new_star_ind], 
        'Probability': [probability_comp_mean]}

print(tabulate(info, headers='keys'))

with open('info.txt', 'w') as f:
    f.write(tabulate(info))

Binary System    Probability
---------------  --------------
[[ 761  765]     [[0.99630895]
 [ 767  770]      [0.99281571]
 [ 893  897]      [0.98947173]
 [2683 2858]]     [0.9989203 ]]


In [47]:
prob_comp_mean_step1 = np.reshape(prob_comp_mean_step1, (len(pair_step1_vis_res),1))
info1 = {'Multiple System': [pair_step1_vis_res], 
        'Probability': [prob_comp_mean_step1]}

print(tabulate(info1, headers='keys'))
with open('Multiple Systems Step1.txt', 'w') as f:
    f.write(tabulate(info1))

Multiple System                Probability
-----------------------------  --------------
[['31' 'NaN' '32' 'NaN']       [[0.99680999]
 ['33' 'NaN' '35' 'NaN']        [0.99616204]
 ['34' 'NaN' '35' 'NaN']        [0.99620746]
 ['205' 'NaN' '206' 'NaN']      [0.99864132]
 ['209' 'NaN' '212' 'NaN']      [0.99837064]
 ['257' 'NaN' '261' 'NaN']      [0.9987968 ]
 ['272' 'NaN' '276' 'NaN']      [0.99675901]
 ['356' 'NaN' '358' 'NaN']      [0.99690746]
 ['430' 'NaN' '432' 'NaN']      [0.99408608]
 ['453' 'NaN' '459' 'NaN']      [0.99248878]
 ['570' 'NaN' '575' 'NaN']      [0.99368172]
 ['771' 'NaN' '777' 'NaN']      [0.99712783]
 ['779' 'NaN' '787' 'NaN']      [0.99281228]
 ['784' 'NaN' '795' 'NaN']      [0.97185974]
 ['797' 'NaN' '806' 'NaN']      [0.995694  ]
 ['811' 'NaN' '812' 'NaN']      [0.98967236]
 ['826' 'NaN' '836' 'NaN']      [0.96087759]
 ['827' 'NaN' '838' 'NaN']      [0.94552232]
 ['830' 'NaN' '833' 'NaN']      [0.99242894]
 ['842' 'NaN' '844' 'NaN']      [0.96308359]
 ['843' 'Na

In [48]:
CORRprob_comp_mean_step2 = np.reshape(CORRprob_comp_mean_step2, (len(CORRpair_step2_vis),1))
prob_triple_corr = np.reshape(prob_triple_corr, (len(index_triple_step2),1))
info2 = {'Multiple System': [index_triple_step2, CORRpair_step2_vis], 
        'Probabilities': [prob_triple_corr, CORRprob_comp_mean_step2]}

print(tabulate(info2, headers='keys'))
with open('Multiple Systems Step2.txt', 'w') as f:
    f.write(tabulate(info2))

Multiple System                                         Probabilities
------------------------------------------------------  ---------------
[['820' 'NaN' 'NaN' 'NaN' '827' 'NaN' '838' 'NaN']      [[0.94552232]
 ['994' 'NaN' 'NaN' 'NaN' '1011' 'NaN' '1021' 'NaN']     [0.90360755]
 ['1146' 'NaN' 'NaN' 'NaN' '1158' 'NaN' '1174' 'NaN']    [0.95449742]
 ['1295' 'NaN' 'NaN' 'NaN' '1311' 'NaN' '1315' 'NaN']]   [0.95808068]]
[['674' 'NaN' 'NaN' 'NaN' '680' 'NaN' 'NaN' 'NaN']      [[0.47630257]
 ['678' 'NaN' 'NaN' 'NaN' '681' 'NaN' 'NaN' 'NaN']       [0.48997265]
 ['681' 'NaN' 'NaN' 'NaN' '690' 'NaN' 'NaN' 'NaN']       [0.49952359]
 ['686' 'NaN' 'NaN' 'NaN' '711' 'NaN' 'NaN' 'NaN']       [0.4810702 ]
 ['698' 'NaN' 'NaN' 'NaN' '678' 'NaN' 'NaN' 'NaN']       [0.47060988]
 ['773' 'NaN' 'NaN' 'NaN' '791' 'NaN' 'NaN' 'NaN']       [0.48604955]
 ['785' 'NaN' 'NaN' 'NaN' '805' 'NaN' 'NaN' 'NaN']       [0.45886162]
 ['815' 'NaN' 'NaN' 'NaN' '829' 'NaN' 'NaN' 'NaN']       [0.3661532 ]
 ['852' 'NaN' 'Na

In [49]:
prob_comp_mean_step3_corr = np.reshape(prob_comp_mean_step3_corr, (len(pair_step3_vis_res),1))
info3 = {'Multiple System': [pair_step3_vis_res], 
        'Probabilities': [prob_comp_mean_step3_corr]}

print(tabulate(info3, headers='keys'))
with open('Multiple Systems Step3.txt', 'w') as f:
    f.write(tabulate(info3))

Multiple System                                                            Probabilities
-------------------------------------------------------------------------  ---------------
[['30' 'NaN' 'NaN' 'NaN' 'NaN' 'NaN' 'NaN' 'NaN' '31' 'NaN' '32' 'NaN'     [[0.90481623]
  'NaN' 'NaN' 'NaN' 'NaN']                                                  [0.92117893]
 ['200' 'NaN' 'NaN' 'NaN' 'NaN' 'NaN' 'NaN' 'NaN' '201' 'NaN' 'NaN' 'NaN'   [0.91194644]
  'NaN' 'NaN' 'NaN' 'NaN']                                                  [0.96193883]
 ['322' 'NaN' 'NaN' 'NaN' 'NaN' 'NaN' 'NaN' 'NaN' '327' 'NaN' 'NaN' 'NaN'   [0.96767764]
  'NaN' 'NaN' 'NaN' 'NaN']                                                  [0.91984893]
 ['807' 'NaN' 'NaN' 'NaN' 'NaN' 'NaN' 'NaN' 'NaN' '837' 'NaN' 'NaN' 'NaN'   [0.97039144]
  'NaN' 'NaN' 'NaN' 'NaN']                                                  [0.98641633]
 ['1232' 'NaN' 'NaN' 'NaN' 'NaN' 'NaN' 'NaN' 'NaN' '1280' 'NaN' 'NaN'       [0.9976479 ]
  'NaN' 'NaN' 'NaN'

In [50]:
prob_comp_mean_step4_corr = np.reshape(prob_comp_mean_step4_corr, (len(pair_step4_vis_res),1))
info4 = {'Multiple System': [pair_step4_vis_res], 
        'Probabilities': [prob_comp_mean_step4_corr]}

print(tabulate(info4, headers='keys'))

with open('Multiple Systems Step4.txt', 'w') as f:
    f.write(tabulate(info4))

Multiple System                               Probabilities
--------------------------------------------  ---------------
[['29' 'NaN' 'NaN' ... 'NaN' 'NaN' 'NaN']     [[0.88584225]
 ['116' 'NaN' 'NaN' ... 'NaN' 'NaN' 'NaN']     [0.97407201]
 ['252' 'NaN' 'NaN' ... 'NaN' 'NaN' 'NaN']     [0.66712211]
 ...                                           [0.86262081]
 ['2380' 'NaN' 'NaN' ... 'NaN' 'NaN' 'NaN']    [0.64165904]
 ['2517' 'NaN' 'NaN' ... 'NaN' 'NaN' 'NaN']    [0.68721394]
 ['2521' 'NaN' 'NaN' ... 'NaN' 'NaN' 'NaN']]   [0.66044727]
                                               [0.71671266]
                                               [0.83313132]
                                               [0.75689613]
                                               [0.8477595 ]
                                               [0.77770466]
                                               [0.83642303]
                                               [0.7089166 ]
                                      

In [51]:
import pandas as pd
d = {
    'Multiple_System': [pair_step4_vis_res],
    'Probabilities': [prob_comp_mean_step4_corr], 
}
df = pd.DataFrame(data=d)
df

Multiple_System  \
0  [[29, NaN, NaN, NaN, NaN, NaN, NaN, NaN, NaN, ...   

                                       Probabilities  
0  [[0.8858422471171964], [0.9740720128121206], [...

In [52]:
from tabulate import tabulate

probability_comp_mean = np.reshape(probability_comp_mean, (4,1))
CORRprob_comp_mean_step2 = np.reshape(CORRprob_comp_mean_step2, (len(CORRpair_step2_vis),1))
prob_triple_corr = np.reshape(prob_triple_corr, (len(index_triple_step2),1))
prob_comp_mean_step1 = np.reshape(prob_comp_mean_step1, (len(pair_step1_vis_res),1))

info = {'Multiple System': [new_star_ind, pair_step1_vis_res, index_triple_step2, CORRpair_step2_vis], 
        'Probabilities': [probability_comp_mean, prob_comp_mean_step1, prob_triple_corr, CORRprob_comp_mean_step2]}

print(tabulate(info, headers='keys'))

with open('info.txt', 'w') as f:
    f.write(tabulate(info))

Multiple System                                         Probabilities
------------------------------------------------------  ---------------
[[ 761  765]                                            [[0.99630895]
 [ 767  770]                                             [0.99281571]
 [ 893  897]                                             [0.98947173]
 [2683 2858]]                                            [0.9989203 ]]
[['31' 'NaN' '32' 'NaN']                                [[0.99680999]
 ['33' 'NaN' '35' 'NaN']                                 [0.99616204]
 ['34' 'NaN' '35' 'NaN']                                 [0.99620746]
 ['205' 'NaN' '206' 'NaN']                               [0.99864132]
 ['209' 'NaN' '212' 'NaN']                               [0.99837064]
 ['257' 'NaN' '261' 'NaN']                               [0.9987968 ]
 ['272' 'NaN' '276' 'NaN']                               [0.99675901]
 ['356' 'NaN' '358' 'NaN']                               [0.99690746]
 ['430' 'NaN' '43

In [53]:
test=0
for i in range(len(pair_step3_vis_res)):
  if prob_comp_mean_step4_corr[i] >= 0.91:
    print(pair_step4_vis_res[i])
    print(prob_comp_mean_step4_corr[i])
    test=test+1
print(test)

['116' 'NaN' 'NaN' 'NaN' 'NaN' 'NaN' 'NaN' 'NaN' 'NaN' 'NaN' 'NaN' 'NaN'
 'NaN' 'NaN' 'NaN' 'NaN' '119' 'NaN' 'NaN' 'NaN' 'NaN' 'NaN' 'NaN' 'NaN'
 'NaN' 'NaN' 'NaN' 'NaN' 'NaN' 'NaN' 'NaN' 'NaN']
[0.97407201]
1


In [54]:
for i in range(len(pair_step3_vis_res)):
  print(prob_comp_mean_step3_corr[i])
  print(pair_step3_vis_res[i])

[0.90481623]
['30' 'NaN' 'NaN' 'NaN' 'NaN' 'NaN' 'NaN' 'NaN' '31' 'NaN' '32' 'NaN'
 'NaN' 'NaN' 'NaN' 'NaN']
[0.92117893]
['200' 'NaN' 'NaN' 'NaN' 'NaN' 'NaN' 'NaN' 'NaN' '201' 'NaN' 'NaN' 'NaN'
 'NaN' 'NaN' 'NaN' 'NaN']
[0.91194644]
['322' 'NaN' 'NaN' 'NaN' 'NaN' 'NaN' 'NaN' 'NaN' '327' 'NaN' 'NaN' 'NaN'
 'NaN' 'NaN' 'NaN' 'NaN']
[0.96193883]
['807' 'NaN' 'NaN' 'NaN' 'NaN' 'NaN' 'NaN' 'NaN' '837' 'NaN' 'NaN' 'NaN'
 'NaN' 'NaN' 'NaN' 'NaN']
[0.96767764]
['1232' 'NaN' 'NaN' 'NaN' 'NaN' 'NaN' 'NaN' 'NaN' '1280' 'NaN' 'NaN' 'NaN'
 'NaN' 'NaN' 'NaN' 'NaN']
[0.91984893]
['1512' 'NaN' 'NaN' 'NaN' 'NaN' 'NaN' 'NaN' 'NaN' '1551' 'NaN' 'NaN' 'NaN'
 'NaN' 'NaN' 'NaN' 'NaN']
[0.97039144]
['1548' 'NaN' 'NaN' 'NaN' 'NaN' 'NaN' 'NaN' 'NaN' '1562' 'NaN' 'NaN' 'NaN'
 'NaN' 'NaN' 'NaN' 'NaN']
[0.98641633]
['2229' 'NaN' 'NaN' 'NaN' 'NaN' 'NaN' 'NaN' 'NaN' '2230' 'NaN' 'NaN' 'NaN'
 'NaN' 'NaN' 'NaN' 'NaN']
[0.9976479]
['2287' 'NaN' 'NaN' 'NaN' 'NaN' 'NaN' 'NaN' 'NaN' '2293' 'NaN' 'NaN' 'NaN'
 'NaN' 'NaN'

In [55]:
print(prob_comp_mean_step3_corr)
print(len(prob_comp_mean_step3_corr))
print(pair_step3_vis_res)
print(len(pair_step3_vis_res))

[[0.90481623]
 [0.92117893]
 [0.91194644]
 [0.96193883]
 [0.96767764]
 [0.91984893]
 [0.97039144]
 [0.98641633]
 [0.9976479 ]
 [0.95162415]
 [0.95254365]
 [0.98064083]
 [0.90038389]
 [0.92097695]
 [0.9698115 ]
 [0.95714348]
 [0.94138281]
 [0.96247161]
 [0.99203213]]
19
[['30' 'NaN' 'NaN' 'NaN' 'NaN' 'NaN' 'NaN' 'NaN' '31' 'NaN' '32' 'NaN'
  'NaN' 'NaN' 'NaN' 'NaN']
 ['200' 'NaN' 'NaN' 'NaN' 'NaN' 'NaN' 'NaN' 'NaN' '201' 'NaN' 'NaN' 'NaN'
  'NaN' 'NaN' 'NaN' 'NaN']
 ['322' 'NaN' 'NaN' 'NaN' 'NaN' 'NaN' 'NaN' 'NaN' '327' 'NaN' 'NaN' 'NaN'
  'NaN' 'NaN' 'NaN' 'NaN']
 ['807' 'NaN' 'NaN' 'NaN' 'NaN' 'NaN' 'NaN' 'NaN' '837' 'NaN' 'NaN' 'NaN'
  'NaN' 'NaN' 'NaN' 'NaN']
 ['1232' 'NaN' 'NaN' 'NaN' 'NaN' 'NaN' 'NaN' 'NaN' '1280' 'NaN' 'NaN'
  'NaN' 'NaN' 'NaN' 'NaN' 'NaN']
 ['1512' 'NaN' 'NaN' 'NaN' 'NaN' 'NaN' 'NaN' 'NaN' '1551' 'NaN' 'NaN'
  'NaN' 'NaN' 'NaN' 'NaN' 'NaN']
 ['1548' 'NaN' 'NaN' 'NaN' 'NaN' 'NaN' 'NaN' 'NaN' '1562' 'NaN' 'NaN'
  'NaN' 'NaN' 'NaN' 'NaN' 'NaN']
 ['2229' 'NaN' 'NaN'